In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib.patches as patches
import numpy as np
import os
import math
from matplotlib.animation import FuncAnimation
from matplotlib.patches import Rectangle, FancyArrowPatch
import seaborn as sns

In [2]:
session_df = pd.read_csv("D:\FOVmeasure\Measures\measures\model_sessionplot_df.csv")
Asession_df = pd.read_csv("D:\FOVmeasure\Measures\measures\model_Asessionplot_df.csv")
trial_df = pd.read_csv("D:\FOVmeasure\Measures\measures\model_trial_df.csv")

In [3]:
#input some set up
#target point(-2.85,0.108).position point(-2.85,-0.623),width0.71,height1.256,and the rader postion0.45,
# Define the target point
target_x = -2.025
rader_x = 0.45
target_y = 0

 # Define the vertices of the hexagon in (x,y) coordinate pairs
vertices = [(-2.5, -1.37), (-2.5, 1.486), (-0.04,  1.486), (-0.04, 1.123), (0.8465, 1.123), (0.8465, -1.37)]

# Define the target area position, width, and height.target point(-2.85,0.108).position point(-2.85,-0.623),width0.71,height1.256,and the rader postion error 0.32
rect_pos = (-2.2,-0.314 )
rect_width = 0.35
rect_height = 0.628

robot_width = 0.4

criterion_dis = 4
criterion_Yr = 0.314

criterion_Yr_2 = 0.628

x_range = (-2.8,1.8)
y_range = (-1.8,1.8)
time_range = (0,180)
Y_range = (0,0.5)

# Define the path to the directory containing the data, the path to store the output 

diskaddress = "D:/FOVmeasure/"

Measures_dir = os.path.join(diskaddress,"Measures/")
data_dir = os.path.join(Measures_dir,"data/")
Pdata_dir = os.path.join(Measures_dir,"Pdata/")
plot_dir = os.path.join(Measures_dir,"plot/")
plotA_dir = os.path.join(Measures_dir,"plot/Acrossfish")

Baselinedata_dir = os.path.join(diskaddress,"Rawdata/Baselinedata/")
Rotationdata_dir = os.path.join(diskaddress,"Rawdata/Rotationdata/")
Washoutdata_dir = os.path.join(diskaddress,"Rawdata/Washoutdata/")
ReRotationdata_dir = os.path.join(diskaddress,"Rawdata/ReRotationdata/")
ReWashoutdata_dir = os.path.join(diskaddress,"Rawdata/ReWashoutdata/")
fishmeasures_dir = os.path.join(Measures_dir,"measures/")


# Create the directory if it does not exist
if not os.path.exists(Measures_dir):
    os.makedirs(Measures_dir)
if not os.path.exists(Pdata_dir):
    os.makedirs(Pdata_dir)
# Create the directory if it does not exist
if not os.path.exists(fishmeasures_dir):
    os.makedirs(fishmeasures_dir)
    # Create the directory if it does not exist
if not os.path.exists(plot_dir):
    os.makedirs(plot_dir)
if not os.path.exists(plotA_dir):
    os.makedirs(plotA_dir)
# Define a list of stages in the correct order
stages = ['Baseline', 'Rotation', 'Washout', 'ReRotation','ReWashout']
stages_BWR= ['Baseline', 'Rotation', 'Washout']
stages_RReR= ['Rotation', 'ReRotation']
stages_ReRReW= [ 'ReRotation', 'ReWashout']
stages_RW = ['Rotation', 'Washout']


# Define color mapping for trial phases
phase_colors = {
    'Baseline': '#F0E442',  # Yellow
    'Rotation': '#CC79A7',   # Reddish Purple
    'Washout': '#F0E442',  # Yellow
    'ReRotation': '#56B4E9',  # Sky Blue
    'ReWashout':   '#E69F00',  # Orange
}
phase_colors_BWR = {
    'Baseline': '#F0E442',  # Yellow
    'Rotation': '#CC79A7',   # Reddish Purple
    'Washout': '#F0E442',  # Yellow
}




In [4]:
def overlap_success(row): 
    if row['Xr'] < rect_pos[0] + rect_width:
        if  np.abs(row['Yr']) < (criterion_Yr - robot_width/2):
            return 1
        elif  np.abs(row['Yr']) >= (criterion_Yr - robot_width/2) and np.abs(row['Yr']) < (criterion_Yr + robot_width/2):
            return (criterion_Yr + robot_width/2-np.abs(row['Yr']))/robot_width
    return 0


def Edirection_trial(row):
    if math.atan2(row['Yr'] , row['Xr']) >0:
        return 3.14 - math.atan2(row['Yr'] , row['Xr'])
    elif math.atan2(row['Yr'] , row['Xr']) <0:
        return -1*3.14 - math.atan2(row['Yr'] , row['Xr'])
    else:
        return 0
    


def fancy_distacne(row) :
    if row['OESuc'] == 0:
        return row['ds'] + row['Edis']
    else:
        return row['ds'] 
    
def fancy_completed_distacne(row) :
    if row['OESuc'] == 0:
        return row['ds'] + row['Edis']*row['sum_ds']/row['sum_SEdis']
    else:
        return row['ds'] 

def calculate_success(row):
    if row['Xr'] < rect_pos[0] + rect_width and criterion_Yr * (-1) < row['Yr'] < criterion_Yr:
        return 1
    else:
        return 0


In [5]:
def calculate_patched_success(row):
    if row['Xr'] < rect_pos[0] + rect_width:
        if -criterion_Yr < row['Yr'] < criterion_Yr:
            return 1
        elif -criterion_Yr_2 < row['Yr'] < criterion_Yr_2:
            return 0.5
    return 0


def calculate_patched_ds(row):
    if row['ds'] < 2.0:
        return 8
    if row['ds'] < 8 and row['Xr'] > 0:
        return 8
    return row['ds']

  


def model_trial_data(input_csv, output_csv):
    # Step 1: Read the input CSV file
    df = input_csv
    
    # Step 2: Select specific columns
    selected_columns = ['Xr', 'Yr', 'date', 'trial', 'fish_id', 'session','ds','Yds','Edis','trial_id','day','plotday']
    df_selected = df[selected_columns]
    

    df_selected['PESuc'] = df_selected.apply(calculate_patched_success, axis=1)

    df_selected['Pds'] = df_selected.apply(calculate_patched_ds, axis=1)

    df_selected['OESuc'] = df_selected.apply(overlap_success, axis=1)

    df_selected['EDir'] = df_selected.apply(Edirection_trial, axis=1)

    
    df_selected['Fdis'] = df_selected.apply(fancy_distacne,axis=1)

    # Step 3: Apply the calculate_success function to each row
    df_selected['ESuc'] = df_selected.apply(calculate_success, axis=1)
    
    # Step 6: Save the new DataFrame to a new CSV file
    df_selected.to_csv(output_csv, index=False)



In [6]:
Pdata_trial_file = os.path.join(Pdata_dir, 'Ptrial.csv')
Pdata_session_file = os.path.join(Pdata_dir, 'Psession.csv')
Pdata_sessionplot_file = os.path.join(Pdata_dir, 'Psessionplot.csv')



In [7]:
model_trial_data(trial_df,Pdata_trial_file)

C:\Users\86153\AppData\Local\Temp\ipykernel_34224\1645991014.py:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_selected['PESuc'] = df_selected.apply(calculate_patched_success, axis=1)
C:\Users\86153\AppData\Local\Temp\ipykernel_34224\1645991014.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_selected['Pds'] = df_selected.apply(calculate_patched_ds, axis=1)
C:\Users\86153\AppData\Local\Temp\ipykernel_34224\1645991014.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a sli

In [8]:
Pdata_trial = pd.read_csv(Pdata_trial_file)

In [9]:
# Pdata_trial['EDire'] = 0
Pdata_trial['EDire'] = np.rad2deg(Pdata_trial['EDir'])

Pdata_trial['SEdis'] = np.sqrt(Pdata_trial['Xr']**2+Pdata_trial['Yr']**2)

sum_ds = Pdata_trial.groupby(['fish_id', 'plotday'])['ds'].sum().rename('sum_ds')
sum_SEdis = Pdata_trial.groupby(['fish_id', 'plotday'])['SEdis'].sum().rename('sum_SEdis')

    
Pdata_trial = pd.merge(Pdata_trial, sum_ds, how='left', on=['fish_id', 'plotday'])
Pdata_trial = pd.merge(Pdata_trial, sum_SEdis, how='left', on=['fish_id', 'plotday'])



In [10]:

Pdata_trial['Fcompletedis'] = Pdata_trial.apply(fancy_completed_distacne,axis=1)

In [11]:
Pdata_trial.to_csv(Pdata_trial_file, index=False)

In [12]:
def calculate_session_csv(input_df,output_file):
    # Calculate median distances and median Yds for each plot day and fish ID
    median_distances = input_df.groupby(['fish_id', 'plotday'])['ds'].median().rename('mediandistance')
    median_Yds = input_df.groupby(['fish_id', 'plotday'])['Yds'].median().rename('medianYds')
   # median_YdsPds = input_df.groupby(['fish_id', 'plotday'])['YdsPds'].median().rename('medianYdsPds')
    median_EDire = input_df.groupby(['fish_id', 'plotday'])['EDire'].median().rename('medianEDire')
    median_Fdis = input_df.groupby(['fish_id', 'plotday'])['Fdis'].median().rename('medianFdis')
    median_FCdis = input_df.groupby(['fish_id', 'plotday'])['Fcompletedis'].median().rename('medianFCdis')

    mean_Yds = input_df.groupby(['fish_id', 'plotday'])['Yds'].mean().rename('meanYds')
    mean_distance = input_df.groupby(['fish_id', 'plotday'])['ds'].mean().rename('meandistance') 
   # mean_YdsPds = input_df.groupby(['fish_id', 'plotday'])['YdsPds'].mean().rename('meanYdsPds')
    mean_EDire = input_df.groupby(['fish_id', 'plotday'])['EDire'].mean().rename('meanEDire')
    

    input_df['cos_mean'] = input_df['EDir'].apply(lambda x: np.cos(x))
    input_df['sin_mean'] = input_df['EDir'].apply(lambda x: np.sin(x))

    sum_cos_mean = input_df.groupby(['fish_id', 'plotday'])['cos_mean'].sum().rename('sum_cos')
    sum_sin_mean = input_df.groupby(['fish_id', 'plotday'])['sin_mean'].sum().rename('sum_sin')

    # Merge the median calculations back into input_df based on fish ID and plot day
    input_df = pd.merge(input_df, median_distances, how='left', on=['fish_id', 'plotday'])
    input_df = pd.merge(input_df, median_Yds, how='left', on=['fish_id', 'plotday'])
    #input_df = pd.merge(input_df, median_YdsPds, how='left', on=['fish_id', 'plotday'])
    input_df = pd.merge(input_df, median_EDire, how='left', on=['fish_id', 'plotday'])
    input_df = pd.merge(input_df, median_Fdis, how='left', on=['fish_id', 'plotday'])
    input_df = pd.merge(input_df, median_FCdis, how='left', on=['fish_id', 'plotday'])

    input_df = pd.merge(input_df, mean_distance, how='left', on=['fish_id', 'plotday'])
    input_df = pd.merge(input_df, mean_Yds, how='left', on=['fish_id', 'plotday'])   
    #input_df = pd.merge(input_df, mean_YdsPds, how='left', on=['fish_id', 'plotday'])
    input_df = pd.merge(input_df, mean_EDire, how='left', on=['fish_id', 'plotday'])   

    
    input_df = pd.merge(input_df, sum_cos_mean, how='left', on=['fish_id', 'plotday'])
    input_df = pd.merge(input_df, sum_sin_mean, how='left', on=['fish_id', 'plotday'])


    input_df['PEST'] = 0
    for i in range(1, len(input_df)):
        if (input_df['plotday'].iloc[i] == input_df['plotday'].iloc[i-1] and
            input_df['OESuc'].iloc[i] >0):
            input_df['PEST'].iloc[i] =input_df['PEST'].iloc[i-1] + input_df['PESuc'].iloc[i]
        elif (input_df['plotday'].iloc[i] != input_df['plotday'].iloc[i-1] and
            input_df['OESuc'].iloc[i] >0): 
            input_df['PEST'].iloc[i] = input_df['OESuc'].iloc[i]
        elif (input_df['plotday'].iloc[i] == input_df['plotday'].iloc[i-1] and
            input_df['OESuc'].iloc[i] == 0): 
            input_df['PEST'].iloc[i] = input_df['PEST'].iloc[i-1]
        elif (input_df['plotday'].iloc[i] != input_df['plotday'].iloc[i-1] and
            input_df['OESuc'].iloc[i] == 0):   
            input_df['PEST'].iloc[i] = 0      

    input_df['EST'] = 0
    for i in range(1, len(input_df)):
        if (input_df['plotday'].iloc[i] == input_df['plotday'].iloc[i-1] and
            input_df['ESuc'].iloc[i] == 1):
            input_df['EST'].iloc[i] =input_df['EST'].iloc[i-1] +1
        elif (input_df['plotday'].iloc[i] != input_df['plotday'].iloc[i-1] and
            input_df['ESuc'].iloc[i] == 1): 
            input_df['EST'].iloc[i] = 1    
        elif (input_df['plotday'].iloc[i] == input_df['plotday'].iloc[i-1] and
            input_df['ESuc'].iloc[i] == 0): 
            input_df['EST'].iloc[i] = input_df['EST'].iloc[i-1]
        elif (input_df['plotday'].iloc[i] != input_df['plotday'].iloc[i-1] and
            input_df['ESuc'].iloc[i] == 0):   
            input_df['EST'].iloc[i] = 0      
    input_df.to_csv(output_file, index=False)



In [13]:
calculate_session_csv(Pdata_trial,Pdata_session_file)

C:\Users\86153\AppData\Local\Temp\ipykernel_34224\3834153313.py:50: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  input_df['PEST'].iloc[i] = input_df['PEST'].iloc[i-1]
C:\Users\86153\AppData\Local\Temp\ipykernel_34224\3834153313.py:50: Setti

In [14]:
Pdata_session = pd.read_csv(Pdata_session_file)

In [15]:
trial_6_df = Pdata_session[Pdata_session['trial_id'] == 6]

In [16]:
trial_6_df['sum_cos'] = trial_6_df['sum_cos']/6
trial_6_df['sum_sin'] = trial_6_df['sum_sin']/6
trial_6_df['circular_mean_radians'] = np.arctan2(trial_6_df['sum_sin'], trial_6_df['sum_cos'])
trial_6_df['circular_mean_degrees'] = np.degrees(trial_6_df['circular_mean_radians'])

C:\Users\86153\AppData\Local\Temp\ipykernel_34224\2024002790.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  trial_6_df['sum_cos'] = trial_6_df['sum_cos']/6
C:\Users\86153\AppData\Local\Temp\ipykernel_34224\2024002790.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  trial_6_df['sum_sin'] = trial_6_df['sum_sin']/6
C:\Users\86153\AppData\Local\Temp\ipykernel_34224\2024002790.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_

In [17]:
trial_6_df.to_csv(Pdata_sessionplot_file , index=False)